In [1]:
# Dictionary. DO NOT EDIT!
from dictionary import dictionary 
ACCIDENT_TYPES_KEY = 'p6'

In [2]:
import pandas as pd
from sklearn.metrics import accuracy_score
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier
from sklearn.tree import plot_tree
import matplotlib.pyplot as plt
from datetime import datetime

# Function to treat missing values
def treatMissingValues(df, column, strategy='mean', fill_value=None):
    if not isinstance(df, pd.DataFrame):
        raise ValueError("Input 'df' must be a pandas DataFrame.")
    
    df_copy = df.copy()

    if column not in df_copy.columns:
        print(f"Column '{column}' not found in the DataFrame.")
        return df_copy
    
    col_dtype = df_copy[column].dtype
    
    if df_copy[column].isnull().sum() == 0:
        print(f"No missing values found in column '{column}'.")
        return df_copy
    
    if strategy == 'mean' and col_dtype in ['int64', 'float64']:
        mean_value = df_copy[column].mean()
        fill_value = round(mean_value)
    elif strategy == 'mode':
        fill_value = df_copy[column].mode()[0]
    elif strategy == 'median' and col_dtype in ['int64', 'float64']:
        fill_value = df_copy[column].median()
    elif strategy == 'ffill':
        df_copy[column].fillna(method='ffill', inplace=True)
        return df_copy
    elif strategy == 'bfill':
        df_copy[column].fillna(method='bfill', inplace=True)
        return df_copy
    elif strategy == 'custom':
        if fill_value is None:
            print("Error: 'fill_value' must be provided when 'strategy' is 'custom'.")
            return df_copy
    else:
        print("Invalid strategy.")
        return df_copy
    
    df_copy[column].fillna(fill_value, inplace=True)
    print(f"Filled missing values in column '{column}' with {strategy}: {fill_value}")
    
    return df_copy


In [3]:
# Load accidents from CSV file
raw_data_accidents = pd.read_csv('output/Inehody_raw.csv',delimiter=';')

# Selected columns that may affect result
data_accidents_column_names = ['p1', 'p5a', 'p6', 'p7', 'p8', 'p8a', 'p10','p11','p11a', 'p12','p13a', 'p13b','p13c','p15', 'p16', 'p17','p18', 'p19', 'p20', 'p21', 'p22', 'p23','p28', 'p36' ]
print(f"Imported {len(data_accidents_column_names)} columns:",[dictionary.get(column, {}).get('label') or column for column in data_accidents_column_names])
data_accidents = raw_data_accidents.loc[:, data_accidents_column_names]

# Make sure they aare unique
unique_p1_accidents = data_accidents['p1'].unique()
data_accidents = pd.merge(data_accidents, pd.DataFrame({'p1': unique_p1_accidents}), on='p1', how='inner')

# Check is unique (same rows)
assert unique_p1_accidents.shape[0] == data_accidents.shape[0], "Dataset is not unique."

# Check for missing values in each column
for column in data_accidents.columns:
    missing_values_count = data_accidents[column].isnull().sum()
    if missing_values_count > 0:
        default_value = dictionary.get(column,{}).get('default')
        if default_value:
            data_accidents = treatMissingValues(df=data_accidents, column=column, strategy='custom', fill_value=default_value)
        else:    
            print(f"Column '{column}' has {missing_values_count} missing value(s). There is no default value defined for '{column}'. Please provide treatment manually.")

# check missing values treatement
missing_values_per_column = data_accidents.isnull().any()
assert not missing_values_per_column.any(), "Columns with missing values: {missing_values_per_column[missing_values_per_column]}"

print(data_accidents)
print(data_accidents.shape)

Imported 24 columns: ['id', 'Lokalita nehody', 'Druh nehody', 'Druh srazky jedouciho vozidel', 'Druh pevne prekazky', 'Typ zvirete', 'Zavineni nehody', 'Pritomnost alkoholu u vinika', 'Pritomnost drog u vinika', 'Hlavni priciny nehody', 'Nehoda s umrtim', 'Nehoda s vaznym zranenim', 'Nehoda s lehkym zranenim', 'Typ povrchu silnice', 'Stav povrchu vozovky v dobe nehody', 'Stav komunikace', 'Povetrnostni podminky v dobe nehody', 'Viditelnosti', 'Rozhledove podminky', 'Deleni komunikace', 'Situovani nehody na komunikaci', 'Rizeni provozu v dobe nehody', 'Smerove pomery', 'Druh pozemni komunikace']
Filled missing values in column 'p8a' with custom: 0
Filled missing values in column 'p11a' with custom: 8
                 p1  p5a  p6  p7  p8  p8a  p10  p11 p11a  p12  ...  p16  p17  \
0       10623000002    2   5   0   0  1.0    4    0  8.0  100  ...    2    1   
1       60223000039    1   3   0   3  0.0    1    0  8.0  508  ...    1    1   
2          23000455    1   1   4   0  0.0    1    2

In [4]:
# Load pedestrians from CSV file
raw_data_pedestrians = pd.read_csv('output/Ichodci_raw.csv',delimiter=';')

# Choose columns that may affect result
data_pedestrians_column_names = ['p1','p29a','p29b','p30a','p30b', 'p31', 'p33c', 'p33d', 'p33f', 'p33g' ]
print(f"Imported {len(data_pedestrians_column_names)} columns:",[dictionary.get(column, {}).get('label') or column for column in data_pedestrians_column_names])
data_pedestrians = raw_data_pedestrians.loc[:, data_pedestrians_column_names]

# Calculate age
current_year = datetime.now().year

def calculate_age(birthday_year):
    try:
        year = int(birthday_year)
        current_year_last_two_digit = current_year % 100
        # Convert to full years
        full_year = 1900 + year if year > current_year_last_two_digit else 2000 + year
        return current_year - full_year
    except (TypeError, ValueError):
        return None
    
# Apply the calculate function
data_pedestrians['p33d'] = data_pedestrians['p33d'].apply(calculate_age)

# Apply treatement mean for age
data_pedestrians = treatMissingValues(df=data_pedestrians, column='p33d', strategy='mean')

# Convert age into group using interval
age_bins = [0, 18, 26, 50, 65, 80, float('inf')]
data_pedestrians['age_group'] = pd.cut(data_pedestrians['p33d'], bins=age_bins, right=False)
# Indexing age_group
unique_age_groups = data_pedestrians['age_group'].unique()
# Create a mapping from age groups to index numbers
age_group_index = {age_group: index for index, age_group in enumerate(unique_age_groups)}
data_pedestrians['age_group'] = data_pedestrians['age_group'].map(age_group_index)

# Check for missing values in each column
for column in data_pedestrians.columns:
    missing_values_count = data_pedestrians[column].isnull().sum()
    if missing_values_count > 0:
        default_value = dictionary.get(column,{}).get('default')
        if default_value:
            data_pedestrians = treatMissingValues(df=data_pedestrians, column=column, strategy='custom', fill_value=default_value)
        else:    
            print(f"Column '{column}' has {missing_values_count} missing value(s). There is no default value defined for '{column}'. Please provide treatment manually.")


# check missing values treatement
missing_values_per_column = data_pedestrians.isnull().any()
assert not missing_values_per_column.any(), "Columns with missing values: {missing_values_per_column[missing_values_per_column]}"

print(data_pedestrians)
print(data_pedestrians.shape)

Imported 10 columns: ['id', 'Reflexni prvky u chodce', 'Chodec na osobnim prepravniku', 'Pritomnost alkoholu (Chodec)', 'Druhy drogy u chodce', 'Chovani chodce', 'Pohlavi chodce', 'Rok narozeni chodce (posledni dvojcisli)', 'Poskytnuti prvni pomoci', 'Nasledky pro chodce']
Filled missing values in column 'p33d' with mean: 48
Filled missing values in column 'p29a' with custom: 2
Filled missing values in column 'p29b' with custom: 2
Filled missing values in column 'p30a' with custom: 0
Filled missing values in column 'p30b' with custom: 8
                p1 p29a p29b p30a p30b  p31  p33c  p33d  p33f  p33g age_group
0      70623000032  2.0  2.0  0.0  8.0    1     2  79.0     6     3         0
1      70623000013  2.0  2.0  2.0  8.0    2     2  47.0     2     3         1
2      70323000011  2.0  2.0  2.0  0.0    1     4  13.0     3     3         2
3         23003157  2.0  2.0  2.0  8.0    1     1  81.0     1     4         3
4     180523000030  2.0  2.0  2.0  0.0    1     1   7.0     5     3

In [5]:
data = pd.merge(data_accidents, data_pedestrians, on='p1', how='right')
total_missing_values = data.isnull().sum().sum()

print("Merged data:", data)

Merged data:                 p1  p5a  p6  p7  p8  p8a  p10  p11 p11a  p12  ...  p29a  p29b  \
0      70623000032    1   4   0   0  0.0    1    0  0.0  412  ...   2.0   2.0   
1      70623000013    1   4   0   0  0.0    3    2  0.0  100  ...   2.0   2.0   
2      70323000011    1   4   0   0  0.0    1    0  8.0  506  ...   2.0   2.0   
3         23003157    1   4   0   0  0.0    1    0  8.0  412  ...   2.0   2.0   
4     180523000030    1   4   0   0  0.0    1    2  8.0  412  ...   2.0   2.0   
...            ...  ...  ..  ..  ..  ...  ...  ...  ...  ...  ...   ...   ...   
3286      23013936    1   4   0   0  0.0    1    2  8.0  412  ...   2.0   2.0   
3287   70123000784    1   4   0   0  0.0    1    2  0.0  508  ...   2.0   2.0   
3288   20323000286    1   4   0   0  0.0    1    2  8.0  508  ...   2.0   2.0   
3289   20323000286    1   4   0   0  0.0    1    2  8.0  508  ...   2.0   2.0   
3290  170623001589    1   4   0   0  0.0    3    2  8.0  100  ...   2.0   2.0   

      p30a  p3

In [6]:
#Test data
# Same rows
assert data_pedestrians.shape[0] <= data.shape[0]

In [7]:
X = data.drop(['p1', 'p13a', 'p13b', 'p13c', 'p33d', 'p33g'], axis=1)
y = data.loc[:, ['p33g']]

# Splitting the data into train and test sets

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42) # 30/70
models = {}
for column in y.columns:
    clf = DecisionTreeClassifier()
    clf.fit(X_train, y_train[column])
    models[column] = clf

# Evaluate the Model
accuracies = {}
for column in y.columns:
    y_pred = models[column].predict(X_test)
    accuracies[column] = accuracy_score(y_test[column], y_pred)
    print(f"Accuracy for {dictionary.get(column,{}).get('label')}: {accuracies[column]}")

Accuracy for Nasledky pro chodce: 0.7540485829959515


In [8]:

plt.figure(figsize=(15, 5), dpi=1000)
for i, column in enumerate(y.columns, start=1):
    plt.subplot(1, len(y.columns), i)
    features = [dictionary.get(name, {}).get('label', name) for name in models[column].feature_names_in_]
    class_labels = [str(label) if label not in [0, 1] else "True" if label == 1 else "False" for label in models[column].classes_]
    plot_tree(models[column], filled=True, feature_names=features, class_names=class_labels)
    plt.title(f"Decision Tree for {dictionary.get(column,{}).get('label')}")
plt.tight_layout()
plt.show()

In [18]:
# Test

def translate_and_print_example(example):
    example_name = example.name
    translated_keys = [dictionary.get(key, {}).get('label', key) for key in example.index]
    translated_values = [dictionary.get(key, {}).get('items', {}).get(str(int(value)), value) for key, value in example.items()]
    prediction = models['p33g'].predict([example]) 
    result = prediction[0]
    label = dictionary.get('p33g', {}).get('items', {}).get(str(result), result)

    print(f"{example_name}: >>")
    for key, value, translated_value in zip(translated_keys, example, translated_values):
        print(f"{key}: {translated_value if translated_value != value else value}")
    print("Prediction:", label, " <<")

translate_and_print_example(X_test.iloc[160])
translate_and_print_example(X_test.iloc[161])


1651: >>
Lokalita nehody: v obci
Druh nehody: srazka s chodcem
Druh srazky jedouciho vozidel: neprichazi v uvahu - nejedna se o srazku jedoucich vozidel
Druh pevne prekazky: nepříchází v úvahu (nejedná se o srážku s pevnou překážkou)
Typ zvirete: nejde o srážku se zvěří/zvířetem
Zavineni nehody: řidičem motorového vozidla
Pritomnost alkoholu u vinika: Ne
Pritomnost drog u vinika: ne
Hlavni priciny nehody: chodci na vyznačeném přechodu
Typ povrchu silnice: živice
Stav povrchu vozovky v dobe nehody: povrch mokrý
Stav komunikace: dobrý, bez závad
Povetrnostni podminky v dobe nehody: neztížené
Viditelnosti: ve dne, viditelnost nezhoršená vlivem povětrnostních podmínek
Rozhledove podminky: dobré
Deleni komunikace: dvoupruhová
Situovani nehody na komunikaci: na jízdním pruhu
Rizeni provozu v dobe nehody: žádný způsob řízení provozu
Smerove pomery: přímý úsek
Druh pozemni komunikace: silnice 1. tridy
Reflexni prvky u chodce: ne
Chodec na osobnim prepravniku: ne
Pritomnost alkoholu (Chodec): n

/Users/luckykiet/anaconda3/lib/python3.11/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but DecisionTreeClassifier was fitted with feature names
  warnings.warn(
/Users/luckykiet/anaconda3/lib/python3.11/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but DecisionTreeClassifier was fitted with feature names
  warnings.warn(
